In [1]:
import os
import pandas as pd
import datetime
import re

# Function to list all chat files in the directory structure
def list_chat_files(date_directory):
    chat_files = []
    for date_folder in os.listdir(date_directory):
        date_path = os.path.join(date_directory, date_folder)
        if os.path.isdir(date_path):
            for team_folder in os.listdir(date_path):
                team_path = os.path.join(date_path, team_folder)
                if os.path.isdir(team_path):
                    for person_folder in os.listdir(team_path):
                        person_path = os.path.join(team_path, person_folder)
                        if os.path.isdir(person_path):
                            for file in os.listdir(person_path):
                                if file.endswith('.txt'):
                                    chat_files.append(os.path.join(person_path, file))
    return chat_files

def parse_chat_file(file_path):
    chat_data = []
    today_minus_one = datetime.datetime.now().date() - datetime.timedelta(days=1)

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            message_match = re.match(r'(\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2} [ap]m) - (.*?): (.*)', line)
            system_match = re.match(r'(\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2} [ap]m) - (.*)', line)
            if message_match:
                date_time_str, sender, message = message_match.groups()
            elif system_match:
                date_time_str, info = system_match.groups()
                sender = None
            else:
                continue

            date_time = pd.to_datetime(date_time_str, format='%d/%m/%y, %I:%M %p')

            # Comparing parsed date with today - 1
            if date_time.date() != today_minus_one:
                continue

            # Adjusted logic to check for numeric sender (phone number)
            is_person = sender is not None and re.match(r'^[+\d\s-]+$', sender) is None  # True if sender is NOT purely numeric

            chat_data.append((date_time, sender, is_person))
    return chat_data



# Function to create a template dataframe
def create_template_dataframe():
    times = [datetime.datetime(2000, 1, 1, 0, 0) + datetime.timedelta(minutes=1 * i) for i in range(1440)]
    intervals = [time.strftime('%I:%M %p') for time in times]
    df = pd.DataFrame(index=intervals)
    return df

def populate_dataframe(df, parsed_data, start_column_index):
    new_columns = {}  # Dictionary to hold new data before concatenation

    for entry in parsed_data:
        date_time, sender, is_person = entry
        interval_index = min((date_time.hour * 60 + date_time.minute) // 1, 1439)
        interval = df.index[interval_index]

        print(f"Processing entry: {entry}, Interval: {interval}")  # Debug line

        # Initialize columns in new_columns dictionary if not exist
        if (start_column_index not in new_columns):
            new_columns[start_column_index] = pd.Series(0, index=df.index)
            print(f"Initialized new column: {start_column_index}")  # Debug line
        if (start_column_index + 1 not in new_columns):
            new_columns[start_column_index + 1] = pd.Series(0, index=df.index)
            print(f"Initialized new column: {start_column_index + 1}")  # Debug line

        # Populate the new_columns dictionary
        if is_person:
            new_columns[start_column_index].at[interval] = 1
            print(f"Populated person column {start_column_index} at interval {interval}")  # Debug line
        else:
            new_columns[start_column_index + 1].at[interval] = 1
            print(f"Populated system column {start_column_index + 1} at interval {interval}")  # Debug line

    print(f"New columns to be added: {new_columns.keys()}")  # Debug line

    # Concatenate new columns to the DataFrame at once
    df = pd.concat([df, pd.DataFrame(new_columns)], axis=1)
    print("Concatenated new columns to DataFrame")  # Debug line

    print(f"DataFrame after concatenation: {df.head()}")  # Debug line to show the top rows of the DataFrame

    return df, start_column_index + 2



def process_person_chats(chat_files):
    dataframes = {}
    for file in chat_files:
        parts = file.split(os.sep)
        date_folder, person = parts[-4], parts[-2]

        try:
            expected_date = pd.to_datetime(date_folder).date()
        except ValueError:
            print(f"Skipping file due to incorrect date format in folder name: {file}")
            continue

        key = f"{expected_date.strftime('%Y-%m-%d')}_{person}"

        if key not in dataframes:
            dataframes[key] = create_template_dataframe()
            start_column_index = 0
        else:
            if not dataframes[key].columns.empty:
                start_column_index = max(dataframes[key].columns) + 1
            else:
                start_column_index = 0

        # Updated call to parse_chat_file
        parsed_data = parse_chat_file(file)
        next_column_index = populate_dataframe(dataframes[key], parsed_data, start_column_index)
        # Use the returned DataFrame to update the dictionary
        dataframes[key], start_column_index = populate_dataframe(dataframes[key], parsed_data, start_column_index)
    
    return dataframes



# Main script
date_directory = "C:\\Users\\maurice\\Documents\\Chat-Analyzer-V2\\Chat Folder from Drive\\drive-download-20231130T060206Z-001"
chat_files = list_chat_files(date_directory)
person_dataframes = process_person_chats(chat_files)




Processing entry: (Timestamp('2023-11-29 08:27:00'), 'Aditi Edoofa', True), Interval: 08:27 AM
Initialized new column: 0
Initialized new column: 1
Populated person column 0 at interval 08:27 AM
Processing entry: (Timestamp('2023-11-29 08:28:00'), '+263 78 039 4189', False), Interval: 08:28 AM
Populated system column 1 at interval 08:28 AM
Processing entry: (Timestamp('2023-11-29 08:28:00'), '+263 78 039 4189', False), Interval: 08:28 AM
Populated system column 1 at interval 08:28 AM
Processing entry: (Timestamp('2023-11-29 08:32:00'), 'Aditi Edoofa', True), Interval: 08:32 AM
Populated person column 0 at interval 08:32 AM
Processing entry: (Timestamp('2023-11-29 08:32:00'), 'Aditi Edoofa', True), Interval: 08:32 AM
Populated person column 0 at interval 08:32 AM
Processing entry: (Timestamp('2023-11-29 08:32:00'), 'Aditi Edoofa', True), Interval: 08:32 AM
Populated person column 0 at interval 08:32 AM
Processing entry: (Timestamp('2023-11-29 08:32:00'), 'Aditi Edoofa', True), Interval: 

Processing entry: (Timestamp('2023-11-29 13:33:00'), 'Aditi Edoofa', True), Interval: 01:33 PM
Initialized new column: 6
Initialized new column: 7
Populated person column 6 at interval 01:33 PM
Processing entry: (Timestamp('2023-11-29 14:51:00'), '+263 78 548 6225', False), Interval: 02:51 PM
Populated system column 7 at interval 02:51 PM
Processing entry: (Timestamp('2023-11-29 14:52:00'), 'Aditi Edoofa', True), Interval: 02:52 PM
Populated person column 6 at interval 02:52 PM
Processing entry: (Timestamp('2023-11-29 14:52:00'), 'Aditi Edoofa', True), Interval: 02:52 PM
Populated person column 6 at interval 02:52 PM
Processing entry: (Timestamp('2023-11-29 15:01:00'), '+263 78 548 6225', False), Interval: 03:01 PM
Populated system column 7 at interval 03:01 PM
Processing entry: (Timestamp('2023-11-29 15:17:00'), 'Aditi Edoofa', True), Interval: 03:17 PM
Populated person column 6 at interval 03:17 PM
Processing entry: (Timestamp('2023-11-29 15:25:00'), '+91 70272 84972', False), Interv

Processing entry: (Timestamp('2023-11-29 08:14:00'), 'Aditi Edoofa', True), Interval: 08:14 AM
Initialized new column: 12
Initialized new column: 13
Populated person column 12 at interval 08:14 AM
Processing entry: (Timestamp('2023-11-29 08:14:00'), 'Aditi Edoofa', True), Interval: 08:14 AM
Populated person column 12 at interval 08:14 AM
Processing entry: (Timestamp('2023-11-29 08:34:00'), '+91 78146 59163', False), Interval: 08:34 AM
Populated system column 13 at interval 08:34 AM
Processing entry: (Timestamp('2023-11-29 08:46:00'), 'Aditi Edoofa', True), Interval: 08:46 AM
Populated person column 12 at interval 08:46 AM
Processing entry: (Timestamp('2023-11-29 09:19:00'), '+91 78146 59163', False), Interval: 09:19 AM
Populated system column 13 at interval 09:19 AM
Processing entry: (Timestamp('2023-11-29 09:52:00'), 'Aditi Edoofa', True), Interval: 09:52 AM
Populated person column 12 at interval 09:52 AM
Processing entry: (Timestamp('2023-11-29 10:19:00'), '+91 78146 59163', False), 

Concatenated new columns to DataFrame
DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  \
12:00 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
12:01 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
12:02 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
12:03 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
12:04 AM   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

          17  
12:00 AM   0  
12:01 AM   0  
12:02 AM   0  
12:03 AM   0  
12:04 AM   0  
Processing entry: (Timestamp('2023-11-29 13:31:00'), 'Aditi Edoofa', True), Interval: 01:31 PM
Initialized new column: 16
Initialized new column: 17
Populated person column 16 at interval 01:31 PM
Processing entry: (Timestamp('2023-11-29 16:30:00'), 'Aditi Edoofa', True), Interval: 04:30 PM
Populated person column 16 at interval 04:30 PM
Processing entry: (T

DataFrame after concatenation:           0   1   2   3   4   5   6   7   8   9   ...  14  15  16  17  18  19  \
12:00 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   
12:01 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   
12:02 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   
12:03 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   
12:04 AM   0   0   0   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   

          20  21  22  23  
12:00 AM   0   0   0   0  
12:01 AM   0   0   0   0  
12:02 AM   0   0   0   0  
12:03 AM   0   0   0   0  
12:04 AM   0   0   0   0  

[5 rows x 24 columns]
Processing entry: (Timestamp('2023-11-29 13:08:00'), 'Aditi Edoofa', True), Interval: 01:08 PM
Initialized new column: 24
Initialized new column: 25
Populated person column 24 at interval 01:08 PM
New columns to be added: dict_keys([24, 25])
Concatenated new columns to DataFrame
DataFrame after c

...

Processing entry: (Timestamp('2023-11-29 07:43:00'), 'Shubham Madhwal', True), Interval: 07:43 AM
Initialized new column: 130
Initialized new column: 131
Populated person column 130 at interval 07:43 AM
Processing entry: (Timestamp('2023-11-29 07:50:00'), '+263 77 387 0363', False), Interval: 07:50 AM
Populated system column 131 at interval 07:50 AM
Processing entry: (Timestamp('2023-11-29 08:12:00'), 'Shubham Madhwal', True), Interval: 08:12 AM
Populated person column 130 at interval 08:12 AM
Processing entry: (Timestamp('2023-11-29 08:13:00'), 'Shubham Madhwal', True), Interval: 08:13 AM
Populated person column 130 at interval 08:13 AM
Processing entry: (Timestamp('2023-11-29 08:38:00'), '+263 77 387 0363', False), Interval: 08:38 AM
Populated system column 131 at interval 08:38 AM
Processing entry: (Timestamp('2023-11-29 08:55:00'), 'Shubham Madhwal', True), Interval: 08:55 AM
Populated person column 130 at interval 08:55 AM
Processing entry: (Timestamp('2023-11-29 09:44:00'), '+263

DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  128  129  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:01 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:02 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:03 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:04 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          130  131  132  133  134  135  136  137  
12:00 AM    0    0    0    0    0    0    0    0  
12:01 AM    0    0    0    0    0    0    0    0  
12:02 AM    0    0    0    0    0    0    0    0  
12:03 AM    0    0    0    0    0    0    0    0  
12:04 AM    0    0    0    0    0    0    0    0  

[5 rows x 138 columns]
Processing entry: (Timestamp('2023-11-29 09:44:00'), 'Shubham Madhwal', True), Interval: 09:44 AM
Initialized new column: 136
Initialized new column: 137
Populated person colum

DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  132  133  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:01 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:02 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:03 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:04 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          134  135  136  137  138  139  140  141  
12:00 AM    0    0    0    0    0    0    0    0  
12:01 AM    0    0    0    0    0    0    0    0  
12:02 AM    0    0    0    0    0    0    0    0  
12:03 AM    0    0    0    0    0    0    0    0  
12:04 AM    0    0    0    0    0    0    0    0  

[5 rows x 142 columns]
Processing entry: (Timestamp('2023-11-29 07:44:00'), 'Shubham Madhwal', True), Interval: 07:44 AM
Initialized new column: 140
Initialized new column: 141
Populated person colum

Concatenated new columns to DataFrame
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  138  139  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:01 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:02 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:03 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:04 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          140  141  142  143  144  145  146  147  
12:00 AM    0    0    0    0    0    0    0    0  
12:01 AM    0    0    0    0    0    0    0    0  
12:02 AM    0    0    0    0    0    0    0    0  
12:03 AM    0    0    0    0    0    0    0    0  
12:04 AM    0    0    0    0    0    0    0    0  

[5 rows x 148 columns]
Processing entry: (Timestamp('2023-11-29 09:58:00'), 'Shubham Madhwal', True), Interval: 09:58 AM
Initialized new column: 146
Initialized 

[5 rows x 154 columns]
Processing entry: (Timestamp('2023-11-29 22:18:00'), '+263 71 729 5968', False), Interval: 10:18 PM
Initialized new column: 152
Initialized new column: 153
Populated system column 153 at interval 10:18 PM
New columns to be added: dict_keys([152, 153])
Concatenated new columns to DataFrame
DataFrame after concatenation:           0    1    2    3    4    5    6    7    8    9    ...  144  145  \
12:00 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:01 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:02 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:03 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   
12:04 AM    0    0    0    0    0    0    0    0    0    0  ...    0    0   

          146  147  148  149  150  151  152  153  
12:00 AM    0    0    0    0    0    0    0    0  
12:01 AM    0    0    0    0    0    0    0    0  
12:02 AM    0    0    0    0    0    0  

In [ ]:
person_dataframes

In [2]:
# Save each dataframe as a CSV file in the current working directory for testing purpose only, will be omiited in real application

for key, df in person_dataframes.items():
    csv_file_path = f"csvs/{key}.csv"
    df.to_csv(csv_file_path)
    print(f"Saved DataFrame to {csv_file_path}")

Saved DataFrame to csvs/2023-11-30_Aditi_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Ananya_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Jasmine_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Saloni_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Sharda_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Ashi_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Kirti Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Milan_Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Shivjeet Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Arshita.csv
Saved DataFrame to csvs/2023-11-30_Austin#276.csv
Saved DataFrame to csvs/2023-11-30_Harmehak.csv
Saved DataFrame to csvs/2023-11-30_Pallika Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Sagar.csv
Saved DataFrame to csvs/2023-11-30_Sahil Edoofa.csv
Saved DataFrame to csvs/2023-11-30_Shashwat Edoofa 2.csv
Saved DataFrame to csvs/2023-11-30_Shubham Madhwal.csv
Saved DataFrame to csvs/2023-11-30_Tushti.csv
